<a href="https://colab.research.google.com/github/KirellosY/MedAppointments-using-dash/blob/main/PlotlyNoteBook.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import kagglehub
joniarroba_noshowappointments_path = kagglehub.dataset_download('joniarroba/noshowappointments')

print('Data source import complete.')


Data source import complete.


In [ ]:
!pip install dash

# Imports & General Checks

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from dash import html,dcc,Dash

In [ ]:
df = pd.read_csv(joniarroba_noshowappointments_path + '/' +'KaggleV2-May-2016.csv')

In [ ]:
df.head()

PatientId  AppointmentID Gender          ScheduledDay  \
0  2.987250e+13        5642903      F  2016-04-29T18:38:08Z   
1  5.589978e+14        5642503      M  2016-04-29T16:08:27Z   
2  4.262962e+12        5642549      F  2016-04-29T16:19:04Z   
3  8.679512e+11        5642828      F  2016-04-29T17:29:31Z   
4  8.841186e+12        5642494      F  2016-04-29T16:07:23Z   

         AppointmentDay  Age      Neighbourhood  Scholarship  Hipertension  \
0  2016-04-29T00:00:00Z   62    JARDIM DA PENHA            0             1   
1  2016-04-29T00:00:00Z   56    JARDIM DA PENHA            0             0   
2  2016-04-29T00:00:00Z   62      MATA DA PRAIA            0             0   
3  2016-04-29T00:00:00Z    8  PONTAL DE CAMBURI            0             0   
4  2016-04-29T00:00:00Z   56    JARDIM DA PENHA            0             1   

   Diabetes  Alcoholism  Handcap  SMS_received No-show  
0         0           0        0             0      No  
1         0           0        0             0      No  
2         0           0        0             0      No  
3         0           0        0             0      No  
4         1           0        0             0      No

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 110527 entries, 0 to 110526
Data columns (total 14 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   PatientId       110527 non-null  float64
 1   AppointmentID   110527 non-null  int64  
 2   Gender          110527 non-null  object 
 3   ScheduledDay    110527 non-null  object 
 4   AppointmentDay  110527 non-null  object 
 5   Age             110527 non-null  int64  
 6   Neighbourhood   110527 non-null  object 
 7   Scholarship     110527 non-null  int64  
 8   Hipertension    110527 non-null  int64  
 9   Diabetes        110527 non-null  int64  
 10  Alcoholism      110527 non-null  int64  
 11  Handcap         110527 non-null  int64  
 12  SMS_received    110527 non-null  int64  
 13  No-show         110527 non-null  object 
dtypes: float64(1), int64(8), object(5)
memory usage: 11.8+ MB


In [ ]:
df['AppointmentDate'] = pd.to_datetime(df['AppointmentDay'])
df['ScheduledDate'] = pd.to_datetime(df['ScheduledDay'])
df['AppointmentDay']=df['AppointmentDate'].dt.day_name()
df['ScheduledDay']=df['ScheduledDate'].dt.day_name()

In [ ]:
df['WaitingDays'] = df['AppointmentDate'] - df['ScheduledDate']

In [ ]:
df['WaitingDays'].min()

Timedelta('-7 days +10:10:40')

In [ ]:
df = df[df['WaitingDays']>pd.Timedelta(0)]

In [ ]:
df['WaitingDays'] = df['WaitingDays'].dt.days

In [ ]:
df['No-show'].value_counts()

No-show
No     51437
Yes    20522
Name: count, dtype: int64

In [ ]:
df.isna().sum()

PatientId          0
AppointmentID      0
Gender             0
ScheduledDay       0
AppointmentDay     0
Age                0
Neighbourhood      0
Scholarship        0
Hipertension       0
Diabetes           0
Alcoholism         0
Handcap            0
SMS_received       0
No-show            0
AppointmentDate    0
ScheduledDate      0
WaitingDays        0
dtype: int64

In [ ]:
df.duplicated().sum()

np.int64(0)

In [ ]:
df.drop(['PatientId','AppointmentID'],axis=1,inplace=True)

In [ ]:
df.describe()

Age   Scholarship  Hipertension      Diabetes    Alcoholism  \
count  71959.000000  71959.000000  71959.000000  71959.000000  71959.000000   
mean      38.502564      0.092706      0.208897      0.074723      0.025320   
std       22.925421      0.290021      0.406523      0.262946      0.157096   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%       19.000000      0.000000      0.000000      0.000000      0.000000   
50%       39.000000      0.000000      0.000000      0.000000      0.000000   
75%       57.000000      0.000000      0.000000      0.000000      0.000000   
max      115.000000      1.000000      1.000000      1.000000      1.000000   

            Handcap  SMS_received   WaitingDays  
count  71959.000000  71959.000000  71959.000000  
mean       0.020025      0.493086     14.642018  
std        0.154072      0.499956     16.494334  
min        0.000000      0.000000      0.000000  
25%        0.000000      0.000000      3.000000  
50%        0.000000      0.000000      8.000000  
75%        0.000000      1.000000     21.000000  
max        4.000000      1.000000    178.000000

# Columns except Date

In [ ]:
df['Age'].min()
# df['Age'].max()

0

In [ ]:
df = df[df['Age'].between(0, 120)]

In [ ]:
px.histogram(df,x='Age',title='Age Distribution')

In [ ]:
neighbourhood_counts = df['Neighbourhood'].value_counts().reset_index()
neighbourhood_counts.columns = ['Neighbourhood', 'Count']

top_5_neighbourhoods = neighbourhood_counts.head(5)

fig = px.bar(top_5_neighbourhoods, y='Neighbourhood', x='Count', orientation='h',
             title='Top 5 Distribution of Neighbourhoods')
fig.update_layout(yaxis={'categoryorder':'total ascending'})
fig.show()

In [ ]:
df['Gender'].value_counts()

Gender
F    48070
M    23889
Name: count, dtype: int64

In [ ]:
df['Gender'] = df['Gender'].map({'M':'Male','F':'Female'})
px.pie(df,names='Gender',title='Gender Percentage',color_discrete_sequence=['pink','#19d3f3'])

In [ ]:
df['Scholarship']=df['Scholarship'].map({0:'No',1:'Yes'})
px.pie(df,names='Scholarship',title='Scholarship Percentage',color_discrete_sequence=['#FFA15A', '#19D3F3'])

In [ ]:
df['Alcoholism']= df['Alcoholism'].map({0:'No',1:'Yes'})
px.pie(df,names='Alcoholism',title='Alcoholism Percentage',color_discrete_sequence=[ '#00CC96', '#AB63FA'])

In [ ]:
px.pie(df,names='No-show',title='No-show Percentage',color_discrete_sequence=['#FF6692','#19d3f3'])

#####*So most of the patients attended their appointment but there are about 20% did not*

In [ ]:
df['Handcap'].value_counts()

Handcap
0    70652
1     1185
2      112
3        8
4        2
Name: count, dtype: int64

In [ ]:
df['Hipertension'] = df['Hipertension'].map({0:'No',1:'Yes'})
df['Diabetes'] = df['Diabetes'].map({0:'No',1:'Yes'})
df['Handcap'] = np.where(df['Handcap']>0, 'Yes', 'No')
df['SMS_received'] = df['SMS_received'].map({0:'No',1:'Yes'})

In [ ]:
px.pie(df,names='Hipertension',title='Hipertension Distribution')

In [ ]:
dia=df['Diabetes'].value_counts()
px.bar(dia,x=dia.index,y=dia.values,title='Diabetes Distribution',color=dia.index)

In [ ]:
px.pie(df,names='Handcap',title='Handicap Percentage',color_discrete_sequence=['#FF6692','#19d3f3'])

In [ ]:
sms=df['SMS_received'].value_counts()
px.bar(dia,x=sms.index,y=sms.values,title='Received SMS Distribution')

# Date Analysis

In [ ]:
df['AppointmentDate'].dt.year.value_counts()

AppointmentDate
2016    71959
Name: count, dtype: int64

In [ ]:
AppM=df['AppointmentDate'].dt.month.value_counts()
AppM

AppointmentDate
5    52431
6    17346
4     2182
Name: count, dtype: int64

In [ ]:
px.bar(AppM, x=AppM.index, y='count',
             title='Appointed month Distribution in 2016',
             labels={'x': 'Month'})

In [ ]:
px.bar(df, x=df['AppointmentDay'].value_counts().index, y=df['AppointmentDay'].value_counts().values,
                               title='Appointment Day of Week Distribution', labels={'x': 'Day of Week', 'y': 'Count'})

In [ ]:
df['ScheduledDate'].dt.year.value_counts()

ScheduledDate
2016    71897
2015       62
Name: count, dtype: int64

In [ ]:
df['ScheduledDate'].dt.month.value_counts().sort_index()

ScheduledDate
1        60
2       281
3      3614
4     24286
5     39011
6      4645
11        1
12       61
Name: count, dtype: int64

In [ ]:
scheduled_month_counts = df['ScheduledDate'].dt.month.value_counts().sort_index()
px.bar(x=scheduled_month_counts.index, y=scheduled_month_counts.values,
       title='Scheduled Month Distribution', labels={'x': 'Month', 'y': 'Count'})

In [ ]:
px.bar(df, x=df['ScheduledDay'].value_counts().index, y=df['ScheduledDay'].value_counts().values,
                               title='Scheduled Day of Week Distribution', labels={'x': 'Day of Week', 'y': 'Count'})

In [ ]:
px.histogram(df, x='WaitingDays', title='Waiting Days Distribution')

In [ ]:
df['WaitingDays'].describe()

count    71959.000000
mean        14.642018
std         16.494334
min          0.000000
25%          3.000000
50%          8.000000
75%         21.000000
max        178.000000
Name: WaitingDays, dtype: float64

# NO Show vs Columns

In [ ]:
px.histogram(df,x='Age',color='No-show',title='Age Distribution')

In [ ]:
# Show= df[df['No-show']== 'No']
# Show.head()

Gender ScheduledDay AppointmentDay  Age   Neighbourhood Scholarship  \
5   Female    Wednesday         Friday   76       REPÚBLICA          No   
9   Female    Wednesday         Friday   19       CONQUISTA          No   
10  Female    Wednesday         Friday   30  NOVA PALESTINA          No   
12  Female     Thursday         Friday   22  NOVA PALESTINA         Yes   
13    Male     Thursday         Friday   28  NOVA PALESTINA          No   

   Hipertension Diabetes Alcoholism Handcap SMS_received No-show  \
5           Yes       No         No      No           No      No   
9            No       No         No      No           No      No   
10           No       No         No      No           No      No   
12           No       No         No      No           No      No   
13           No       No         No      No           No      No   

             AppointmentDate             ScheduledDate  WaitingDays AgeGroup  
5  2016-04-29 00:00:00+00:00 2016-04-27 08:36:51+00:00            1      75+  
9  2016-04-29 00:00:00+00:00 2016-04-27 12:48:25+00:00            1    18-34  
10 2016-04-29 00:00:00+00:00 2016-04-27 14:58:11+00:00            1    18-34  
12 2016-04-29 00:00:00+00:00 2016-04-28 11:33:51+00:00            0    18-34  
13 2016-04-29 00:00:00+00:00 2016-04-28 14:52:07+00:00            0    18-34

In [ ]:
NoShow= df[df['No-show']== 'Yes']
NoShow.head()

Gender ScheduledDay AppointmentDay  Age   Neighbourhood Scholarship  \
6   Female    Wednesday         Friday   23      GOIABEIRAS          No   
7   Female    Wednesday         Friday   39      GOIABEIRAS          No   
11    Male      Tuesday         Friday   29  NOVA PALESTINA          No   
17  Female     Thursday         Friday   40       CONQUISTA         Yes   
20  Female    Wednesday         Friday   30  NOVA PALESTINA          No   

   Hipertension Diabetes Alcoholism Handcap SMS_received No-show  \
6            No       No         No      No           No     Yes   
7            No       No         No      No           No     Yes   
11           No       No         No      No          Yes     Yes   
17           No       No         No      No           No     Yes   
20           No       No         No      No           No     Yes   

             AppointmentDate             ScheduledDate  WaitingDays AgeGroup  
6  2016-04-29 00:00:00+00:00 2016-04-27 15:05:12+00:00            1    18-34  
7  2016-04-29 00:00:00+00:00 2016-04-27 15:39:58+00:00            1    35-54  
11 2016-04-29 00:00:00+00:00 2016-04-26 08:44:12+00:00            2    18-34  
17 2016-04-29 00:00:00+00:00 2016-04-28 09:28:57+00:00            0    35-54  
20 2016-04-29 00:00:00+00:00 2016-04-27 07:51:14+00:00            1    18-34

In [ ]:
neighbourNoShow = NoShow['Neighbourhood'].value_counts()
px.bar(neighbourNoShow.head(5), x=neighbourNoShow.head(5).index,
       y=neighbourNoShow.head(5).values, title='Top 5 Neighbourhoods for No Shows')

In [ ]:
sms_noshow = df.groupby('SMS_received')['No-show'].value_counts(normalize=True).unstack().reset_index()
smsM = sms_noshow.melt(id_vars='SMS_received', var_name='No-show', value_name='Proportion')
px.bar(smsM, x='SMS_received', y='Proportion', color='No-show', barmode='group',
                 title='No-show Rate by SMS Received Status')
